## 作業
礙於不是所有同學都有 GPU ，這邊的範例使用的是簡化版本的 ResNet，確保所有同學都能夠順利訓練!


最後一天的作業請閱讀這篇非常詳盡的[文章](https://blog.gtwang.org/programming/keras-resnet-50-pre-trained-model-build-dogs-cats-image-classification-system/)，基本上已經涵蓋了所有訓練　CNN 常用的技巧，請使用所有學過的訓練技巧，盡可能地提高 Cifar-10 的 test data 準確率，截圖你最佳的結果並上傳來完成最後一次的作業吧!

另外這些技巧在 Kaggle 上也會被許多人使用，更有人會開發一些新的技巧，例如使把預訓練在 ImageNet 上的模型當成 feature extractor 後，再拿擷取出的特徵重新訓練新的模型，這些技巧再進階的課程我們會在提到，有興趣的同學也可以[參考](https://www.kaggle.com/insaff/img-feature-extraction-with-pretrained-resnet)

In [1]:
from keras import backend as K
from keras.models import Model
from keras.layers import Flatten, Dense, Dropout
from keras.applications.resnet50 import ResNet50
from keras.optimizers import Adam
from keras.preprocessing.image import ImageDataGenerator
from keras.datasets import cifar10
from keras.utils import to_categorical
from keras.models import Sequential

Using TensorFlow backend.
C:\Anaconda3\lib\site-packages\pandas\compat\_optional.py:106: UserWarning: Pandas requires version '1.2.1' or newer of 'bottleneck' (version '1.2.0' currently installed).
  warnings.warn(msg, UserWarning)


In [2]:
# 讀取資料集並作前處理
(x_train, y_train), (x_test, y_test) = cifar10.load_data()
print('x_train shape:', x_train.shape)
print('x_test shape:', x_test.shape)
print(x_train.shape[0], 'train samples')
print(x_test.shape[0], 'test samples')
x_train = x_train.astype('float32')
x_test = x_test.astype('float32')

x_train = x_train / 255.
x_test = x_test / 255.
y_train = to_categorical(y_train, 10)
y_test = to_categorical(y_test, 10)

x_train shape: (50000, 32, 32, 3)
x_test shape: (10000, 32, 32, 3)
50000 train samples
10000 test samples


In [3]:
'''
net = ResNet50(include_top=False, weights='imagenet', input_tensor=None,
               input_shape=(IMAGE_SIZE[0],IMAGE_SIZE[1],3))
x = net.output
x = Flatten()(x)

# 增加 DropOut layer
x = Dropout(0.5)(x)

# 增加 Dense layer，以 softmax 產生個類別的機率值
output_layer = Dense(NUM_CLASSES, activation='softmax', name='softmax')(x)

# 設定凍結與要進行訓練的網路層
net_final = Model(inputs=net.input, outputs=output_layer)
for layer in net_final.layers[:FREEZE_LAYERS]:
    layer.trainable = False
for layer in net_final.layers[FREEZE_LAYERS:]:
    layer.trainable = True
'''

"\nnet = ResNet50(include_top=False, weights='imagenet', input_tensor=None,\n               input_shape=(IMAGE_SIZE[0],IMAGE_SIZE[1],3))\nx = net.output\nx = Flatten()(x)\n\n# 增加 DropOut layer\nx = Dropout(0.5)(x)\n\n# 增加 Dense layer，以 softmax 產生個類別的機率值\noutput_layer = Dense(NUM_CLASSES, activation='softmax', name='softmax')(x)\n\n# 設定凍結與要進行訓練的網路層\nnet_final = Model(inputs=net.input, outputs=output_layer)\nfor layer in net_final.layers[:FREEZE_LAYERS]:\n    layer.trainable = False\nfor layer in net_final.layers[FREEZE_LAYERS:]:\n    layer.trainable = True\n"

In [4]:
IMAGE_SIZE = (32, 32)


rest_model = ResNet50(include_top=False, weights='imagenet', input_tensor=None,
               input_shape=(32,32,3))

    
x = rest_model.output
x = Flatten()(x)

# 增加 DropOut layer
#last_fe = Dropout(0.5)

# 增加 Dense layer，以 softmax 產生個類別的機率值
output_layer = Dense(10, activation='softmax', name='softmax')(x)

newModel = Model(inputs=rest_model.input,outputs=output_layer)

newModel.summary()

C:\Anaconda3\lib\site-packages\keras_applications\resnet50.py:265: UserWarning: The output shape of `ResNet50(include_top=False)` has been changed since Keras 2.2.0.
  warnings.warn('The output shape of `ResNet50(include_top=False)` '


Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 32, 32, 3)    0                                            
__________________________________________________________________________________________________
conv1_pad (ZeroPadding2D)       (None, 38, 38, 3)    0           input_1[0][0]                    
__________________________________________________________________________________________________
conv1 (Conv2D)                  (None, 16, 16, 64)   9472        conv1_pad[0][0]                  
__________________________________________________________________________________________________
bn_conv1 (BatchNormalization)   (None, 16, 16, 64)   256         conv1[0][0]                      
____________________________________________________________________________________________

In [5]:
'''
net_final.compile(optimizer=Adam(lr=1e-5),
                  loss='categorical_crossentropy', metrics=['accuracy'])

# 輸出整個網路結構
print(net_final.summary())

# 訓練模型
net_final.fit_generator(train_batches,
                        steps_per_epoch = train_batches.samples // BATCH_SIZE,
                        validation_data = valid_batches,
                        validation_steps = valid_batches.samples // BATCH_SIZE,
                        epochs = NUM_EPOCHS)
'''

"\nnet_final.compile(optimizer=Adam(lr=1e-5),\n                  loss='categorical_crossentropy', metrics=['accuracy'])\n\n# 輸出整個網路結構\nprint(net_final.summary())\n\n# 訓練模型\nnet_final.fit_generator(train_batches,\n                        steps_per_epoch = train_batches.samples // BATCH_SIZE,\n                        validation_data = valid_batches,\n                        validation_steps = valid_batches.samples // BATCH_SIZE,\n                        epochs = NUM_EPOCHS)\n"

In [6]:
batch_size = 64 # batch 的大小，如果出現 OOM error，請降低這個值
num_classes = 10 # 類別的數量，Cifar 10 共有 10 個類別
epochs = 50 # 訓練整個資料集共 30個循環

import keras.losses as kl

for layer in newModel.layers[:2]:
    layer.trainable = False
for layer in newModel.layers[2:]:
    layer.trainable = True

newModel.compile(loss='categorical_crossentropy',
              optimizer=Adam(lr=1e-5),
              metrics=['accuracy'])

#newModel.compile(optimizer= 'adam' , loss= kl.categorical_crossentropy, metrics=['accuracy'])


In [7]:
history = newModel.fit(x_train, y_train,
                    batch_size=batch_size,
                    epochs=epochs,
                    verbose=1,
                    validation_data=(x_test, y_test))
score = newModel.evaluate(x_test, y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

Train on 50000 samples, validate on 10000 samples
Epoch 1/50
50000/50000 [==============================] - 132s 3ms/step - loss: 2.4388 - accuracy: 0.2622 - val_loss: 6.8718 - val_accuracy: 0.1296